### Rate Limits

- 20 requests every 1 seconds 
- 100 requests every 2 minutes

### First get 10000 match histories.

- First 10 columns are the champions for blue team, red team and the last columns stands for "Blue team won"

In [ ]:
import cassiopeia as cass
import getpass
import random

key = getpass.getpass("Enter Riot API key:")

In [ ]:
cass.set_riot_api_key(key)  # This overrides the value set in your configuration/settings.
cass.set_default_region("KR")

In [ ]:
match = cass.get_match(3492500002)

In [ ]:
(match.blue_team.participants[0]).summoner.ranks[match.queue]

In [ ]:
import pickle as pkl
import os
import pandas as pd
from cassiopeia.datastores.riotapi.common import APIRequestError, APIError
from datapipelines.pipelines import NotFoundError


In [ ]:
def get_lane(participant):
    try:
        lane = participant.lane.name
        if lane =='bot_lane':
            lane = participant.role.name
        return lane
    except AttributeError:
        return 'No info'

In [ ]:
def get_data(i):
    dd = []
    match = cass.get_match(i)
    try:
        version = match.version
        queue = match.queue.value
    except APIRequestError:
        print('Your API key has expired.')
        key = getpass.getpass("Enter new Riot API key:")
        cass.set_riot_api_key(key)
        try:
            version = match.version
            queue = match.queue.value
        except:
            return []
    except:
        return []
        
    if queue in ['RANKED_SOLO_5x5'] and version == '9.1.257.7563':        
        for participant in match.blue_team.participants :
            try:
                lane = get_lane(participant)
                champion = participant.champion.name
                rank = participant.summoner.ranks[match.queue]
                tier = ' '.join([rank.tier.name, rank.division.name])
            except APIRequestError:
                print('Your API key has expired.')
                key = getpass.getpass("Enter new Riot API key:")
                cass.set_riot_api_key(key)
                lane = get_lane(participant)
                champion = participant.champion.name
                rank = participant.summoner.ranks[match.queue]
                tier = ' '.join([rank.tier.name, rank.division.name])
            
            dd.append((lane, participant.champion.name, tier))
            
        for ban in match.blue_team.bans:
            try:
                dd.append(ban.name)
            except AttributeError:
                dd.append('밴없음')
                
        for participant in match.red_team.participants :
            try:
                lane = get_lane(participant)
                champion = participant.champion.name
                rank = participant.summoner.ranks[match.queue]
                tier = ' '.join([rank.tier.name, rank.division.name])
            except APIRequestError:
                print('Your API key has expired.')
                key = getpass.getpass("Enter new Riot API key:")
                cass.set_riot_api_key(key)
                lane = get_lane(participant)
                champion = participant.champion.name
                rank = participant.summoner.ranks[match.queue]
                tier = ' '.join([rank.tier.name, rank.division.name])
            
            dd.append((lane, participant.champion.name, tier))
            
        for ban in match.red_team.bans:
            try:
                dd.append(ban.name)
            except AttributeError:
                dd.append('밴없음')

        dd.append(match.blue_team.win)
        print('Match id {} is valid.'.format(i))
    return dd

# Set start_id and end_id

||start_id|end_id|
|----------|------------|------------|
| Jaewoo   | 3490000000 | 3492500000 |
| Jinyoung | 3492500001 | 3495000000 |
| Hwi      | 3495000001 | 3497500000 |
| Q        | 3497500001 | 3500000000 |

In [ ]:
start_id = 3495067160
end_id = 3497500000
ids = range(start_id, end_id)

dir_name = '{}-{}'.format(start_id, end_id)
os.mkdir(os.path.join('../data/',dir_name))

data = []
user = os.path.realpath('.').split('/')[2]
k=0

In [ ]:
for i in ids:
    try:
        dd = get_data(i)
        if len(dd)!=0:
            data.append(dd)
        if len(data)==2000:
            print("Making {}.pkl.".format(k))
            with open(os.path.join('../data/', dir_name, '{}.pkl'.format(k)), 'wb') as f:
                pkl.dump(data, f)
            k+=1
            data = []
    except:
        print('Error occured for {}'.format(i))
        continue

if len(data)!=0:
    with open(os.path.join('../data/', dir_name, '{}.pkl'.format(k)), 'wb') as f:
        pkl.dump(data, f)
        

Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495071595
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495071596
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495071597
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495071598
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495071599
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/4R3ed4OggpcjOaEwd-frfV5GY6N-XtQ94ZWX3iWf7isoDNU
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/APEzqzcbKT5TfAm7JAZ5BezcEZebnOpawrJ3OnJUTEBa2w
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/XcyarFmMh5VB4C9pQ_jyVT7hDbbEjyUd1w8UZVybmj_uKKs
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/dBE-CIDj7hu3XrwLeSF01xnqCHX6W6b-fDlQpxFT_rIMK28
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/SoM2XMkK703jNeQmOgnkEFrwECLF58BnCG_Mg0vvjdkPuA
Ma

Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/WcYL7m8nVhAJkDBv__XZqJrVOwpWpBAUEOGdeaPKK63eQp0
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/RCPd3xy1SPexzaI6Sd1m7hUeaI9L-RtptGgVhHqvy3riGhU
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/5fiWKLcYjUfR-71jNoYGQCQWDi0G3ZMDg9vZHnIFju0SmIo
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/C-IrTHQGeSTTjAf2YHMqn0FGI3PDyP0pvjMnswiZzC3t-9M
Match id 3495071612 is valid.
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495071613
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495071614
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495071615
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495071616
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495071617
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495071618
Making call: https://k

Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/v0mlAoLBYcMD0JE0nv6D6RaRRXpeP1PAUOkzOgPg0JQK5yI
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/mIQBNi5FHzqeKT-P4z8gJHSTVE3uaPICdAf8MyqeKIPU2_8
Match id 3495071633 is valid.
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495071634
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495071635
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/_rWcXrcxfj1lA8-o5qUBy6NVpxRFgZLQM4kv5_XulERI6g
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/5egCzLQuwLq_sWRABivuslL2vSaa12-1JYadRsMK6FI44eY
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/fDw8R43BYVbcoc7wrlMpf6hY7NlMbw7mrXKJF9q-8lsfJw
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/Og3yatlXZTgPY_pX8Yu2-tFH3Qd4SRDadQM9zXfWrGSrrA
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-

Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/fVxsGI-en7KAn_aKr-wXxbiM7MOzk5-CDvE4U6NWR9rU3Zo
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/fWyJsJfPPf7i8Lvp_DLti6IL31cggS6Mov-XW2ZaMucsoQ
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/7LykTtcIzvlo8rLduntm8QgAlQIJTJ_HcT5H0LFVgqmRdoo
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/fPV78CzS0-sajMqffuha2qhqerRyTZ3l4ApkeEBxomHBTw
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/SEQ9SrnntynqEy6mHl6MRf1wJ8t8c2zB5nEEfqvlPKyLnw
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/Z5GSuNmbQbYpBzYoiT1bTMBDTBBQf-6_dhivSViXTgGMgYU
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/0Jek0nHsYdw3YCpYXs8-ATcmVPdYQHLVkGYFLYLf0ZU0mg
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/0wzHuC3ZxSLpVkDopMlUuLI7YEVC5BMbtUmv7HF22r-c

Match id 3495071666 is valid.
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495071667
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495071668
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495071669
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495071670
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/DbvDD0zHxd_C0VUPjSj6FFKb0FbVkHxuALNT2Jbo3BtwJXc
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/2ajUXUyIREM-1dFD7jxdm5cgrRQlaEKcly8KE9VHs_wO7WM
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/-EuLVEmW2HmU8HlcZyfExuPA6oQ0EJE5rxUoELDrEeHT3f8
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/j9aXan6SJG0QBl2yrX4p3XXV7NjAYO043Fvuh0iwSmw75_8
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/vLkHhVNn_EqKZL1YNuIX5xpNjqz8WtnDhBpuaKMp6DIuqk8
Making call: https://kr.api.riotgames.com/lo

...

Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/34pBkh4jiU1uF4bWAbT559H7-lsHHNjyScaVSa6n5SBk_Q
Error occured for 3495100086
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100087
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100088
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/kbYfP_ixnmtG0RrFxyvivwz6APGNBmcPd74ACaDp-asnrcM
Error occured for 3495100088
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100089
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100090
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100091
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100092
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100093
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/dVMXjHh1jCFw7zCkA6FCTAQSkh837C_qqQQOVLhVGfcVXX0
Error occured for 3495100093
Making call: https

Error occured for 3495100155
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100156
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/9NKsfb5qK3eFj8bpENphkb7WXd7gcKBi7uC017n56RFBcw
Error occured for 3495100156
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100157
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100158
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/WV__DBDPIUDqnuAM-EsEWxzFFobujbQf-H56OLMC9xDC8l4
Error occured for 3495100158
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100159
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100160
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100161
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100162
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100163
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100

Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100229
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100230
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/I4GvlIr_QLYX7d65P8rNFMah8pD_6GhNBg4IyFGZmeuoSqM
Error occured for 3495100230
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100231
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100232
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100233
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100234
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100235
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100236
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100237
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100238
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100239
Making call: https://kr.api.rio

Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/1ylgN5VHDUN-tE_zptkd78_LAYwgR7OMgvHPGjAu9D41two
Error occured for 3495100308
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100309
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100310
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100311
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100312
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100313
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100314
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100315
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/UrtNBJBS1HnAbvD0D2IfnzpxWpRSzqG7Tz3UxjTXq6RksQ
Error occured for 3495100315
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100316
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/SvfxmzcHEUy6drIPV-Sdx

Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100380
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/1t49KJ4H3k15_9st7D-sZSv-6H7kH7kjIBDgJ7z55aZhiA
Error occured for 3495100380
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100381
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100382
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100383
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100384
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100385
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100386
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/4MkP1rEwRmsCjTE4NRGGKADXnWKtbhKFDGwBWD517VZ6XQ
Error occured for 3495100386
Making call: https://kr.api.riotgames.com/lol/match/v4/matches/3495100387
Making call: https://kr.api.riotgames.com/lol/league/v4/positions/by-summoner/Cnj-iT7Km4cSFmKq27xsqU